# Example 9 - Multi-objective optimization for Microwave operating conditions
In this example, we will demonstrate how Bayesian Optimization can perform multi-objective optimization (MOO) and create a Pareto front. In example 8, we find an optimal configuration of the cavity, and now we would like to design the optimal operating condition. Two output variables will be generated from the model: outlet temperature (y1) and efficiency (y2). 

The details of this example is summarized in the table below:

| Key Item | Description |
| :- | :- |
| Goal | Maximization, two objectives |
| Objective function | COMSOL simulation |
| Input (X) dimension	| 2 |
| Output (Y) dimension | 2 |
| Analytical form available?	| No |
| Acqucision function | Expected improvement (EI) |

Next, we will go through each step in Bayesian Optimization.

## 1. Import nextorch and other packages

In [1]:
import os
import sys
import time
import numpy as np
from IPython.display import display

project_path = os.path.abspath(os.path.join(os.getcwd(), '../..'))
sys.path.insert(0, project_path)

from nextorch import bo, io, plotting

## 2. Define the design space
We set the names and units for input parameters and output reponses. Their possible operating ranges are also defined.

In [13]:
# Three input final temperature, heating rate, hold time
X_names = ["P_supply", "U_in"]
X_units = ["W", "m/s"]

# Add the units
X_name_with_unit = []
for i, var in enumerate(X_names):
    if not X_units[i]  == '':
        var = var + ' ('+ X_units[i] + ')'
    X_name_with_unit.append(var)

# Create latex-like strings for plotting purposes
X_name_with_unit_plot = []
for i, var in enumerate(X_names):
    if not X_units[i]  == '':
        var = var + ' ('+ X_units[i] + ')'
    X_name_with_unit_plot.append(var)

# Two output
Y_name_with_unit = ['Temperature (K)', 'Efficiency (%)']

# combine X and Y names
var_names = X_name_with_unit + Y_name_with_unit

# Set the operating range for each parameter
X_ranges = [[10.0, 200.0], [0.005, 0.05]]
            
            
# Get the information of the design space
n_dim = len(X_names) # the dimension of inputs
n_objective = 2 # the dimension of outputs

## 3. Define the initial sampling plan
We don't have an objective function in this example. All the data are collected from simulations. Here we assume we already complete 3 Bayesian Optimization iterations.


In [3]:
X_real = np.array([[100.0, 0.0095], [50.0, 0.0095], [100.0, 0.0475], [200.0, 0.005]])
Y_real = np.array([[317.87, 23.752], [311.39, 25.133], [306.68, 22.24], [342.35, 17.320]])

## 4. Initialize an COMSOLMOOExperiment object
In this example, we use a COMSOLMOOExperiment object, a class designed for multi-objective optimization using COMSOL simulation output. An COMSOLMOOExperiment is a subclass of MOOExperiment. It requires all key components as MOOExperiment. 

Some progress status will be printed out while initializing all single Experiment objects.

In [4]:
#%% Initialize an experimental object 
# Set its name, the files will be saved under the folder with the same name
exp_comsol = bo.COMSOLMOOExperiment("Stub tuner")
# Import the initial data
exp_comsol.input_data(X_real, 
                      Y_real, 
                      X_names=X_names, 
                      X_units=X_units, 
                      X_ranges=X_ranges,
                      unit_flag = False) #input X and Y in real scales

# Set the optimization specifications 
file_name = "../Stub_tuner/comsol_moo_example" # name of objective COMSOL simulation file
comsol_location =  "/home/tychen/comsol54/multiphysics/bin/comsol" # location of the COMSOL program installed
output_file = "../Stub_tuner/simulation_result.csv" # location of the COMSOL simulation output file


# 10 weights, 10 Experiments
n_exp = 6 # number of single Experiments

# Set a weight vector for objective 1
weights_obj_1 = np.linspace(0, 1, n_exp)
weights_obj_2 = 1 - weights_obj_1

# here we set the objective function, minimization by default
exp_comsol.set_optim_specs(weights_obj_1, file_name, comsol_location, output_file, comsol_output_col=[2, 3])

Initializing 6 experiments
Iter 10/100: 9.817651748657227
Iter 20/100: 9.16031265258789
Iter 30/100: 8.954179763793945
Iter 40/100: 8.866762161254883
Iter 50/100: 8.799640655517578
Iter 60/100: 8.783628463745117
Iter 70/100: 8.772850036621094
Iter 80/100: 8.766593933105469
Iter 90/100: 8.764199256896973
Iter 100/100: 8.762655258178711
Initializing experiments 16.67 % 
Iter 10/100: 9.817651748657227
Iter 20/100: 9.16031265258789
Iter 30/100: 8.954179763793945
Iter 40/100: 8.866762161254883
Iter 50/100: 8.799640655517578
Iter 60/100: 8.783628463745117
Iter 70/100: 8.772850036621094
Iter 80/100: 8.766593933105469
Iter 90/100: 8.764199256896973
Iter 100/100: 8.762655258178711
Initializing experiments 33.33 % 
Iter 10/100: 9.817651748657227
Iter 20/100: 9.16031265258789
Iter 30/100: 8.954179763793945
Iter 40/100: 8.866762161254883
Iter 50/100: 8.799640655517578
Iter 60/100: 8.783628463745117
Iter 70/100: 8.772850036621094
Iter 80/100: 8.766593933105469
Iter 90/100: 8.764199256896973
Iter 10

## 5. Run trials
At each weight combinations, we perform an optimization task for the scalarized objective (a single Experiment). COMSOLMOOExperiment.run_exp_auto run these tasks automatically by using the default choice of acqucision function, Expected improvement (EI). It takes in the number of trials required for each Experiment. The number of trials needs to be large enough which allows Bayesian Optimization algorithm to converge to the optimum. In this example, the evalution would be slow since the total number of calls for the objective function is n_trails * n_exp (=120).

Some progress status will be printed out during the training.

In [5]:
# Set the number of iterations for each experiments
n_trials = 20 
# Set a timer
start_time = time.time()
exp_comsol.run_exp_auto(n_trials)

end_time = time.time()
print('Optimizing {} Experiments takes {:.2f} minutes.'.format(n_exp, (end_time-start_time)/60))

Running 6 experiments
COMSOL file is sucessfully compiled. Simulation starts.
b'*******************************************'
b'***COMSOL 5.4.0.388 progress output file***'
b'*******************************************'
b'Fri Mar 05 17:48:02 EST 2021'
b'COMSOL Multiphysics 5.4 (Build: 388) starting in batch mode'
b'Running: /home/tychen/Desktop/PhD/nextorch/examples/notebooks/../Stub_tuner/comsol_moo_example_0.class'
b'---------- Current Progress: 100 % - Updating selections'
b'Memory: 424/424 5895/5895'
b'           Current Progress:   0 % - Work Plane 1'
b'Memory: 458/458 5899/5899'
b'           Current Progress:   0 % - Rectangle 1'
b'           Current Progress:   1 % - cavity_mid'
b'Memory: 460/460 5899/5899'
b'-          Current Progress:  11 % - Work Plane 2'
b'Memory: 462/462 5899/5899'
b'-          Current Progress:  11 % - Rectangle 1'
b'-          Current Progress:  13 % - Stub_tuner'
b'Memory: 463/463 5899/5899'
b'--         Current Progress:  22 % - Work Plane 4'
b'--      

b'Symmetric matrices found.'
b'Scales for dependent variables:'
b'Temperature (comp1.T): 3e+02'
b'Nonsymmetric matrix found.'
b'Step        Time    Stepsize      Res  Jac  Sol Order Tfail NLfail   LinErr   LinRes'
b'Nonsymmetric matrix found.'
b'------     Current Progress:  68 % - Solving linear system'
b'Memory: 1894/2310 6678/7247'
b'------     Current Progress:  68 % - Assembling matrices'
b'------     Current Progress:  68 % -'
b'Memory: 1897/2310 6678/7247'
b'------     Current Progress:  68 % - Assembling matrices'
b'------     Current Progress:  68 % - Solving linear system'
b'------     Current Progress:  68 % - Assembling matrices'
b'------     Current Progress:  68 % - Solving linear system'
b'Memory: 1899/2310 6742/7247'
b'------     Current Progress:  68 % - Assembling matrices'
b'   0           0           - out   40    8   40                  0'
b'                   Group #1:       20    4   20                     9.6e-14  1.1e-13'
b'                   Group #2:       20

b'------     Current Progress:  68 % - Matrix factorization'
b'------     Current Progress:  68 % - Assembling matrices'
b'  16  0.00040937  3.1973e-11      280   68  280     1    14      0'
b'                   Group #1:      140   34  140                     2.1e-08  2.5e-05'
b'                   Group #2:      140   34  140                     5.6e-16  4.5e-16'
b'------     Current Progress:  68 % - Constraint handling'
b'------     Current Progress:  68 % - Assembling matrices'
b'  17  0.00040937  3.1973e-11      292   70  292     1    14      0'
b'                   Group #1:      146   35  146                     5.3e-07  5.1e-06'
b'                   Group #2:      146   35  146                     5.6e-16  4.5e-16'
b'  18  0.00040937  6.3946e-11      302   72  302     1    14      0'
b'                   Group #1:      151   36  151                     8.5e-08  2.3e-07'
b'                   Group #2:      151   36  151                     5.3e-16  4.3e-16'
b'  19  0.00040937  6

b'------     Current Progress:  68 % - Solving linear system'
b'  41   0.0004096   6.548e-08      496  118  496     1    14      0'
b'                   Group #1:      248   59  248                     3.5e-09  7.9e-10'
b'                   Group #2:      248   59  248                     5.2e-16  5.4e-16'
b'------     Current Progress:  68 % - Assembling matrices'
b'------     Current Progress:  68 % - Matrix factorization'
b'------     Current Progress:  68 % - Assembling matrices'
b'  42  0.00040967   6.548e-08      502  120  502     1    14      0'
b'                   Group #1:      251   60  251                     1.1e-09  2.9e-09'
b'                   Group #2:      251   60  251                     3.5e-16  3.6e-16'
b'------     Current Progress:  68 % - Solving linear system'
b'  43  0.00040973   6.548e-08      508  122  508     1    14      0'
b'                   Group #1:      254   61  254                     1.9e-09  2.8e-09'
b'                   Group #2:      254   61 

b'  63  0.00061089  6.7052e-05      652  162  652     1    14      0'
b'                   Group #1:      326   81  326                     3.5e-12  3.2e-12'
b'                   Group #2:      326   81  326                     5.4e-16  5.3e-16'
b'------     Current Progress:  68 % - Assembling matrices'
b'------     Current Progress:  68 % - Matrix factorization'
b'------     Current Progress:  68 % - Assembling matrices'
b'  64  0.00067794  6.7052e-05      656  164  656     1    14      0'
b'                   Group #1:      328   82  328                     1.4e-12  2.3e-11'
b'                   Group #2:      328   82  328                     4.5e-16  4.7e-16'
b'------     Current Progress:  68 % - Solving linear system'
b'  65  0.00081204   0.0001341      668  166  668     1    14      0'
b'                   Group #1:      334   83  334                     2.3e-13  2.9e-12'
b'                   Group #2:      334   83  334                     5.2e-16  4.9e-16'
b'------     Curren

...

b'------     Current Progress:  68 % - Solving linear system'
b'Memory: 1906/2264 6787/7170'
b'------     Current Progress:  68 % - Assembling matrices'
b'Memory: 1908/2264 6851/7170'
b'  59  0.00028046  1.7819e-07      730  160  730     1    17      0'
b'                   Group #1:      365   80  365                     6.3e-10  1.9e-09'
b'                   Group #2:      365   80  365                     3.9e-16  3.7e-16'
b'------     Current Progress:  68 % - Matrix factorization'
b'Memory: 1914/2264 6851/7170'
b'------     Current Progress:  68 % - Assembling matrices'
b'Memory: 1915/2264 6851/7170'
b'------     Current Progress:  68 % - Solving linear system'
b'------     Current Progress:  68 % - Assembling matrices'
b'  60  0.00028082  3.5637e-07      744  162  744     1    17      0'
b'                   Group #1:      372   81  372                     7.1e-11  1.7e-10'
b'                   Group #2:      372   81  372                     4.2e-16  4.3e-16'
b'  61  0.00028153 

b'------     Current Progress:  68 % - Assembling matrices'
b'  79     0.18712    0.093421     1004  200 1004     1    17      0'
b'                   Group #1:      502  100  502                     1.7e-13  5.2e-12'
b'                   Group #2:      502  100  502                     5.7e-16  5.4e-16'
b'------     Current Progress:  68 % - Solving linear system'
b'------     Current Progress:  68 % - Assembling matrices'
b'------     Current Progress:  68 % - Solving linear system'
b'------     Current Progress:  68 % - Assembling matrices'
b'  80     0.37396     0.18684     1018  202 1018     1    17      0'
b'                   Group #1:      509  101  509                       1e-13  3.6e-12'
b'                   Group #2:      509  101  509                     5.8e-16  4.1e-16'
b'------     Current Progress:  68 % - Solving linear system'
b'Memory: 1920/2264 6851/7170'
b'  81     0.74765     0.37368     1032  204 1032     1    17      0'
b'                   Group #1:      516  

b'---------  Current Progress:  99 % - Matrix factorization'
b'---------  Current Progress:  99 % - Assembling matrices'
b'   -          49           - out'
b'---------- Current Progress: 100 % - Assembling matrices'
b'   -          50           - out'
b'  94      53.969           5     1138  230 1138     1    17      0'
b'                   Group #1:      569  115  569                     2.1e-14  1.7e-12'
b'                   Group #2:      569  115  569                     6.3e-16  9.1e-16'
b'Time-stepping completed.'
b'---------- Current Progress: 100 % -'
b'Solution time: 271 s. (4 minutes, 31 seconds)'
b'Physical memory: 1.92 GB'
b'Virtual memory: 6.85 GB'
b'Ended at Mar 6, 2021 1:42:34 AM.'
b'----- Time-Dependent Solver 1 in Study 1/Solution 1 (sol1) -------------------->'
b'           Current Progress:   5 % - Evaluating'
b'Memory: 1884/2264 6853/7170'
b'Class run time: 315 s.'
b'Saving model: /home/tychen/Desktop/PhD/nextorch/examples/notebooks/../Stub_tuner/comsol_moo_example

b'Time-dependent solver (BDF)'
b'------     Current Progress:  68 % - Time-Dependent Solver 1'
b'Number of degrees of freedom solved for: 16991 (plus 41218 internal DOFs).'
b'------     Current Progress:  68 % - Assembling sparsity pattern'
b'------     Current Progress:  68 % - Assembling matrices'
b'Memory: 1816/2282 6562/7189'
b'Nonsymmetric matrix found.'
b'Scales for dependent variables:'
b'Pressure (comp1.p): 0.11'
b'Velocity field (comp1.u): 1'
b'------     Current Progress:  68 % - Assembling sparsity pattern'
b'Symmetric matrices found.'
b'Scales for dependent variables:'
b'Temperature (comp1.T): 3e+02'
b'Nonsymmetric matrix found.'
b'Step        Time    Stepsize      Res  Jac  Sol Order Tfail NLfail   LinErr   LinRes'
b'------     Current Progress:  68 % - Assembling matrices'
b'Memory: 1817/2282 6562/7189'
b'Nonsymmetric matrix found.'
b'------     Current Progress:  68 % - Matrix factorization'
b'Memory: 1831/2282 6690/7189'
b'------     Current Progress:  68 % - Assembling

b'------     Current Progress:  68 % - Matrix factorization'
b'Memory: 1841/2282 6695/7189'
b'------     Current Progress:  68 % - Assembling matrices'
b'------     Current Progress:  68 % - Matrix factorization'
b'------     Current Progress:  68 % - Assembling matrices'
b'  12  0.00020732  1.7272e-16      334   76  334     1    21      1'
b'                   Group #1:      167   38  167                     0.00059   0.0002'
b'                   Group #2:      167   38  167                     5.6e-16  4.4e-16'
b'------     Current Progress:  68 % - Matrix factorization'
b'Memory: 1842/2282 6696/7189'
b'------     Current Progress:  68 % - Assembling matrices'
b'------     Current Progress:  68 % - Solving linear system'
b'------     Current Progress:  68 % - Assembling matrices'
b'------     Current Progress:  68 % - Matrix factorization'
b'Memory: 1842/2282 6700/7189'
b'------     Current Progress:  68 % - Assembling matrices'
b'------     Current Progress:  68 % - Solving linear s

## 6. Visualize the Pareto front
We can get the Pareto set directly from the COMSOLMOOExperiment object by using COMSOLMOOExperiment.get_optim. We can see a clear tradeoff between temperature and efficiency, and different optimal points are obtained.

In [17]:
# Extract the set of optimal solutions
Y_real_opts, X_real_opts = exp_comsol.get_optim()
weight_names = [r'$\rm w_1$', r'$\rm w_2$'] 

# Parse the optimum into a table
data_opt = io.np_to_dataframe([weights_obj_1, weights_obj_2, X_real_opts, Y_real_opts], weight_names + var_names, n = n_exp)
display(data_opt.round(decimals=5))


$\rm w_1$  $\rm w_2$  P_supply (W)  U_in (m/s)  Temperature (K)  \
0        0.0        1.0          50.0     0.00950        311.39000   
1        0.2        0.8         200.0     0.02363        315.45762   
2        0.4        0.6         200.0     0.00500        342.35000   
3        0.6        0.4         200.0     0.00500        342.35000   
4        0.8        0.2         200.0     0.00500        342.35000   
5        1.0        0.0         200.0     0.00500        342.35000   

   Efficiency (%)  
0        25.13300  
1        24.36014  
2        17.32000  
3        17.32000  
4        17.32000  
5        17.32000